In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory


import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 5GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/hotel-text-data/text.txt
/kaggle/input/avishek-hotel/sentiments.csv


In [2]:

# Some used imports
%matplotlib inline
import pandas as pd
import numpy as np
import os
import glob
import matplotlib as mpl

# Just making the plots look better
mpl.style.use('ggplot')
mpl.rcParams['figure.figsize'] = (8,6)
mpl.rcParams['font.size'] = 12

In [3]:
import nltk
from nltk.tokenize import sent_tokenize

tokenizer = nltk.data.load('tokenizers/punkt/english.pickle')
fp = open("/kaggle/input/hotel-text-data/text.txt")
data = fp.read()
sentences=sent_tokenize(data)

## Sentences to pandas dataframe

In [4]:
df = pd.DataFrame(sentences,columns=["sentences"])

In [5]:
df

sentences
0       The premises are very peaceful and well mainta...
1       The apartment was spacious though basically eq...
2                 We enjoyed the fine pool and good food.
3                   But the hospitality was overwhelming!
4       These people are so friendly and helpful that ...
...                                                   ...
407957    Police were in parking lot as I was pulling in.
407958  People walking through parking lot heading bac...
407959  We were nearly eaten by the bed bugs, more agr...
407960  I would not reccomend this hole even to my wor...
407961                   Next day we needed medical help.

[407962 rows x 1 columns]

## Categories

In [6]:
cleanliness= ["satisfactory", "ample", "hygienic", "proper", "ambience", "odour","dirty","clean","smell","cleanliness"]
service = ["desk", "check in", "check out", "reliable", "fast", "convenient","service","hospitality"]
location= ["railway", "view","station","airport","distance","far","close","train", "metro","transport","market","mall","surrounding","areas","highway","traffic","out","location"]
value= ["price", "amount", "rate", "cheap", "worth", "low", 'money', "economical", "reasonable", "fee", "expensive", "charge","value"]
room= ["bed","bunkbeds","toilet", "bathroom", "shower","dryer","fridge", "space", "spacious", "outdated", "noisy","room"]
food= ["drink","breakfast","spicy", "food","tasty","tea","coffee", "buffet", "bar", "restaurant","dinner","lunch","brunch","delicious"]
facility= ["pool","gym","wifi","spa","internet","wireless","broken","parking","ventilation","maintained","facility","lot","premises"]
staff= ["friendly","helpful","reliable","quick","good","polite","staff"]

In [7]:
from nltk.corpus import wordnet
import string
from nltk import pos_tag
from nltk.corpus import stopwords
from nltk.tokenize import WhitespaceTokenizer
from nltk.stem import WordNetLemmatizer

def clean_text(text):
    # lower text
    text = text.lower()
    # tokenize text and remove puncutation
    text = [word.strip(string.punctuation) for word in text.split(" ")]
    # remove words that contain numbers
    text = [word for word in text if not any(c.isdigit() for c in word)]
    # remove empty tokens
    text = [t for t in text if len(t) > 0]
    # remove words with only one letter
    text = [t for t in text if len(t) > 1]
    # join all
    text = " ".join(text)
    return(text)

# clean text data
df["sentences_clean"] = df["sentences"].apply(lambda x: clean_text(x))

In [8]:
df

sentences  \
0       The premises are very peaceful and well mainta...   
1       The apartment was spacious though basically eq...   
2                 We enjoyed the fine pool and good food.   
3                   But the hospitality was overwhelming!   
4       These people are so friendly and helpful that ...   
...                                                   ...   
407957    Police were in parking lot as I was pulling in.   
407958  People walking through parking lot heading bac...   
407959  We were nearly eaten by the bed bugs, more agr...   
407960  I would not reccomend this hole even to my wor...   
407961                   Next day we needed medical help.   

                                          sentences_clean  
0       the premises are very peaceful and well mainta...  
1       the apartment was spacious though basically eq...  
2                  we enjoyed the fine pool and good food  
3                    but the hospitality was overwhelming  
4       these people are so friendly and helpful that ...  
...                                                   ...  
407957       police were in parking lot as was pulling in  
407958  people walking through parking lot heading bac...  
407959  we were nearly eaten by the bed bugs more agre...  
407960  would not reccomend this hole even to my worst...  
407961                    next day we needed medical help  

[407962 rows x 2 columns]

In [9]:
df1=df[df["sentences_clean"]!= ""]

In [10]:
df1

sentences  \
0       The premises are very peaceful and well mainta...   
1       The apartment was spacious though basically eq...   
2                 We enjoyed the fine pool and good food.   
3                   But the hospitality was overwhelming!   
4       These people are so friendly and helpful that ...   
...                                                   ...   
407957    Police were in parking lot as I was pulling in.   
407958  People walking through parking lot heading bac...   
407959  We were nearly eaten by the bed bugs, more agr...   
407960  I would not reccomend this hole even to my wor...   
407961                   Next day we needed medical help.   

                                          sentences_clean  
0       the premises are very peaceful and well mainta...  
1       the apartment was spacious though basically eq...  
2                  we enjoyed the fine pool and good food  
3                    but the hospitality was overwhelming  
4       these people are so friendly and helpful that ...  
...                                                   ...  
407957       police were in parking lot as was pulling in  
407958  people walking through parking lot heading bac...  
407959  we were nearly eaten by the bed bugs more agre...  
407960  would not reccomend this hole even to my worst...  
407961                    next day we needed medical help  

[407382 rows x 2 columns]

In [11]:
import re
wordlist=[]
for i in df1["sentences_clean"]:
    wordlist.append(re.split('\s+',i))

In [12]:
df1["sentences_clean"][5]

'after small accident with child that needed stitching in the hospital the brought us there and picked us up again and arranged some snacks during the waiting'

In [13]:
np.array(wordlist)

array([list(['the', 'premises', 'are', 'very', 'peaceful', 'and', 'well', 'maintained']),
       list(['the', 'apartment', 'was', 'spacious', 'though', 'basically', 'equipped']),
       list(['we', 'enjoyed', 'the', 'fine', 'pool', 'and', 'good', 'food']),
       ...,
       list(['we', 'were', 'nearly', 'eaten', 'by', 'the', 'bed', 'bugs', 'more', 'agressive', 'than', 'denali', 'bears']),
       list(['would', 'not', 'reccomend', 'this', 'hole', 'even', 'to', 'my', 'worst', 'enemy']),
       list(['next', 'day', 'we', 'needed', 'medical', 'help'])],
      dtype=object)

In [14]:
a=[]
for i in range(len(wordlist)):
    a.append(len(wordlist[i]))

In [15]:
from statistics import mean 

In [16]:
from fuzzywuzzy import fuzz 

In [17]:
def calculate(word,category):
    clean=[]
    for i in range(len(word)):
        sum=0
        sum1=0
        for j in range(len(word[i])):
            sum=sum+fuzz.ratio(word[i][j],category)
        clean.append(sum/a[i])
    return clean

c=[]
for k in cleanliness:
    c.append(calculate(wordlist,k))


In [18]:
c=(np.array(c)).transpose()

In [19]:
cl=[]
for i in c:
    cl.append(mean(i))
cl

[24.7,
 21.285714285714285,
 19.075,
 18.66,
 20.95714285714286,
 19.937037037037037,
 20.945,
 20.268421052631577,
 20.2,
 20.016666666666666,
 21.445454545454545,
 20.433333333333334,
 18.712,
 19.639130434782608,
 21.58125,
 20.376923076923077,
 15.725,
 20.581666666666667,
 22.45,
 25.779999999999998,
 20.666666666666668,
 18.569565217391304,
 23.31111111111111,
 18.8,
 20.076923076923077,
 19.425,
 22.321052631578947,
 19.070833333333333,
 23.333333333333332,
 17.692307692307693,
 21.152631578947368,
 20.35625,
 20.491891891891893,
 21.428571428571427,
 20.7875,
 21.05,
 20.308333333333334,
 20.626315789473683,
 20.0,
 21.624,
 19.821739130434782,
 20.89,
 20.164285714285715,
 20.288888888888888,
 20.014634146341464,
 18.928571428571427,
 21.233333333333334,
 20.414285714285715,
 20.584615384615386,
 19.391111111111112,
 18.729166666666668,
 15.65,
 18.47826086956522,
 18.725,
 21.135714285714286,
 23.164285714285715,
 19.8,
 18.285714285714285,
 19.488888888888887,
 25.0285714285

In [20]:
s=[]
for k in service:
    s.append(calculate(wordlist,k))

In [21]:
s=(np.array(s)).transpose()
se=[]
for i in s:
    se.append(mean(i))

In [22]:
l=[]
for k in location:
    l.append(calculate(wordlist,k))

In [23]:
l=(np.array(l)).transpose()
lo=[]
for i in l:
    lo.append(mean(i))

In [24]:
v=[]
for k in value:
    v.append(calculate(wordlist,k))
v=(np.array(v)).transpose()    
va=[]
for i in v:
    va.append(mean(i))

In [25]:
r=[]
for k in room:
    r.append(calculate(wordlist,k))
r=(np.array(r)).transpose()    
ro=[]
for i in r:
    ro.append(mean(i))

In [26]:
f=[]
for k in food:
    f.append(calculate(wordlist,k))
f=(np.array(f)).transpose()    
fo=[]
for i in f:
    fo.append(mean(i))

In [27]:
fa=[]
for k in facility:
    fa.append(calculate(wordlist,k))
fa=(np.array(fa)).transpose()    
fac=[]
for i in fa:
    fac.append(mean(i))

In [28]:
st=[]
for k in staff:
    st.append(calculate(wordlist,k))
st=(np.array(st)).transpose()    
sta=[]
for i in st:
    sta.append(mean(i))

In [29]:
cl=np.array(cl)
cl

array([24.7       , 21.28571429, 19.075     , ..., 22.79230769,
       19.05      , 20.66666667])

In [30]:
fuzzy=np.c_[cl,se]
fuzzy=np.c_[fuzzy,lo]
fuzzy=np.c_[fuzzy,va]
fuzzy=np.c_[fuzzy,ro]
fuzzy=np.c_[fuzzy,fo]
fuzzy=np.c_[fuzzy,fac]
fuzzy=np.c_[fuzzy,sta]

In [31]:
fuzz

<module 'fuzzywuzzy.fuzz' from '/opt/conda/lib/python3.7/site-packages/fuzzywuzzy/fuzz.py'>

In [32]:
maxpos=[]
for i in fuzzy:
    maximum = np.max(i)
    tu=np.where(i == maximum)
    maxpos.append(tu[0])

In [33]:
for i in maxpos:
    print(i)

[3]
[2]
[4]
[1]
[3]
[1]
[3]
[3]
[2]
[3]
[3]
[2]
[2]
[2]
[2]
[3]
[2]
[2]
[2]
[0]
[3]
[2]
[3]
[2]
[2]
[2]
[0]
[3]
[2]
[2]
[2]
[2]
[3]
[3]
[4]
[4]
[3]
[4]
[3]
[2]
[2]
[3]
[3]
[3]
[1]
[2]
[1]
[3]
[2]
[2]
[3]
[2]
[2]
[3]
[3]
[3]
[2]
[3]
[3]
[3]
[2]
[3]
[4]
[2]
[2]
[2]
[4]
[4]
[2]
[4]
[4]
[4]
[2]
[3]
[2]
[1]
[0]
[3]
[4]
[1]
[2]
[2]
[3]
[7]
[4]
[4]
[2]
[3]
[2]
[2]
[2]
[4]
[3]
[2]
[2]
[3]
[3]
[3]
[4]
[2]
[2]
[3]
[3]
[3]
[4]
[2]
[3]
[2]
[1]
[3]
[3]
[1]
[3]
[2]
[2]
[2]
[3]
[4]
[3]
[3]
[1]
[2]
[3]
[4]
[2]
[3]
[0]
[3]
[4]
[2]
[2]
[2]
[3]
[3]
[3]
[1]
[3]
[3]
[4]
[2]
[0]
[2]
[3]
[7]
[3]
[2]
[3]
[2]
[2]
[3]
[2]
[4]
[3]
[2]
[4]
[2]
[2]
[2]
[2]
[3]
[4]
[3]
[3]
[3]
[0]
[2]
[2]
[3]
[3]
[2]
[1]
[4]
[2]
[2]
[2]
[1]
[3]
[3]
[2]
[2]
[2]
[2]
[4]
[2]
[4]
[4]
[2]
[3]
[1]
[2]
[0]
[3]
[2]
[4]
[1]
[4]
[3]
[1]
[2]
[4]
[2]
[1]
[2]
[3]
[3]
[4]
[3]
[2]
[1]
[2]
[7]
[2]
[2]
[3]
[2]
[3]
[1]
[1]
[3]
[2]
[0]
[1]
[3]
[3]
[4]
[2]
[4]
[2]
[2]
[3]
[2]
[0]
[3]
[2]
[1]
[3]
[2]
[4]
[3]
[3]
[3]
[4]
[2]
[3]
[3]
[2]
[2]
[2]
[4]
[3]
